In [1]:
import newsource.libword as libword
import math
from decimal import *
import pandas as pd
from collections import OrderedDict as odict

datadir = "./3classdata"
window = 3
resolution = 50
shift = 3

In [2]:
import importlib
importlib.reload(libword)

<module 'newsource.libword' from '/_old/UNITO/lezioni/YearI/SecondSem/BDM/progetto/newsource/libword.py'>

In [3]:
# read files from given directory
def readDatadir(datadir):
    import glob
    frames = odict()
    for dfile in glob.glob(datadir+"/*/*.csv"):
        tmp = libword.read_csv(dfile)
        cord, numb = dfile.strip(datadir+'/').strip('.csv').split('/')
        frames[(cord, int(numb))] = tmp
    return frames

In [4]:
originalDfs = readDatadir(datadir)
len(originalDfs)

372

In [5]:
list(originalDfs.keys())

[('Z', 574),
 ('Z', 22),
 ('Z', 579),
 ('Z', 270),
 ('Z', 268),
 ('Z', 563),
 ('Z', 568),
 ('Z', 571),
 ('Z', 269),
 ('Z', 29),
 ('Z', 570),
 ('Z', 274),
 ('Z', 277),
 ('Z', 250),
 ('Z', 583),
 ('Z', 264),
 ('Z', 2),
 ('Z', 11),
 ('Z', 261),
 ('Z', 588),
 ('Z', 258),
 ('Z', 589),
 ('Z', 9),
 ('Z', 12),
 ('Z', 23),
 ('Z', 580),
 ('Z', 576),
 ('Z', 275),
 ('Z', 257),
 ('Z', 577),
 ('Z', 262),
 ('Z', 276),
 ('Z', 578),
 ('Z', 20),
 ('Z', 562),
 ('Z', 263),
 ('Z', 273),
 ('Z', 256),
 ('Z', 30),
 ('Z', 259),
 ('Z', 585),
 ('Z', 31),
 ('Z', 279),
 ('Z', 25),
 ('Z', 565),
 ('Z', 575),
 ('Z', 251),
 ('Z', 278),
 ('Z', 560),
 ('Z', 584),
 ('Z', 14),
 ('Z', 27),
 ('Z', 561),
 ('Z', 265),
 ('Z', 24),
 ('Z', 19),
 ('Z', 10),
 ('Z', 569),
 ('Z', 587),
 ('Z', 559),
 ('Z', 8),
 ('Z', 271),
 ('Z', 272),
 ('Z', 1),
 ('Z', 567),
 ('Z', 582),
 ('Z', 17),
 ('Z', 260),
 ('Z', 5),
 ('Z', 16),
 ('Z', 3),
 ('Z', 267),
 ('Z', 255),
 ('Z', 26),
 ('Z', 249),
 ('Z', 581),
 ('Z', 573),
 ('Z', 28),
 ('Z', 6),
 ('Z'

In [6]:
# normalize between [-1,1]
normalizeDfs = odict()
for k, df in originalDfs.items():
    normalizeDfs[k] = libword.normalize(df)

In [7]:
# discretize on a gaussian interval of 2*resolution steps
discretizeDfs = dict()
interval = libword.gaussian_interval(resolution)
discretizeDfs = libword.parallel(target=libword.discretize, iterable=normalizeDfs, 
                        interval=interval, how="left", n=12)

In [8]:
#print(interval)
#discretizeDfs[0]

In [9]:
# extract words from dataset (from window,shift given)
wordDfs = libword.parallel(target=libword.rolling_window, iterable=discretizeDfs,
                           w=window, s=shift, n=12)

In [10]:
# TF: on single columns (monovariate series) of each dataframe
# associate each series with its 3 most frequent words (according to TF)
tf_Dfs = libword.parallel(target=libword.extract_words, iterable=wordDfs, 
                          how=libword.text_freq, n=12)

In [11]:
#tf_Dfs[0]

In [12]:
wordDfs[('X', 1)]

0                               1   \
0      (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
1      (0.58036, 0.58036, 0.58036)     (0.46898, 0.15881, 0.46898)   
2      (0.51224, 0.33375, 0.04133)    (0.26847, 0.05422, -0.10077)   
3   (-0.02218, -0.24694, -0.43642)  (-0.51224, -0.43642, -0.43642)   
4   (-0.58036, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
5   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
6   (-1.00000, -1.00000, -1.00000)  (-1.00000, -0.58036, -0.51224)   
7   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
8   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
9   (-1.00000, -0.33375, -0.17462)  (-1.00000, -1.00000, -1.00000)   
10     (0.26847, 0.33375, 0.58036)  (-1.00000, -1.00000, -1.00000)   
11     (0.58036, 0.58036, 0.58036)  (-0.58036, -1.00000, -0.30513)   
12     (0.58036, 0.58036, 0.58036)  (-0.33375, -0.28002, -0.22710)   

                                2                               3   \
0      (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
1      (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
2      (0.58036, 0.40993, 0.18279)     (0.51224, 0.46898, 0.31892)   
3    (0.04776, -0.10077, -0.23683)  (-0.00950, -0.02855, -0.29221)   
4   (-0.43642, -0.36759, -0.33375)  (-0.38737, -1.00000, -1.00000)   
5   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
6   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
7   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
8   (-1.00000, -1.00000, -1.00000)  (-1.00000, -0.46898, -0.34987)   
9   (-1.00000, -1.00000, -1.00000)  (-0.19975, -0.16663, -0.06726)   
10  (-1.00000, -1.00000, -1.00000)   (-0.03492, -0.00950, 0.02218)   
11  (-1.00000, -1.00000, -1.00000)     (0.02855, 0.02855, 0.02855)   
12  (-1.00000, -1.00000, -1.00000)     (0.02218, 0.02855, 0.02855)   

                                4                               5   \
0   (-1.00000, -1.00000, -0.46898)     (0.36759, 0.43642, 0.51224)   
1     (-0.16663, 0.24694, 0.05422)     (0.43642, 0.30513, 0.40993)   
2    (-0.13620, -0.29221, 0.06726)     (0.25747, 0.13620, 0.06726)   
3      (0.51224, 0.46898, 0.46898)  (-0.10767, -0.31892, -0.46898)   
4    (0.30513, -0.22710, -0.58036)  (-1.00000, -1.00000, -1.00000)   
5   (-1.00000, -1.00000, -1.00000)  (-1.00000, -1.00000, -1.00000)   
6   (-1.00000, -0.43642, -0.08049)    (-0.38737, 0.05422, 0.58036)   
7      (0.11466, 0.16663, 0.12174)     (0.58036, 0.58036, 0.58036)   
8   (-0.03492, -0.25747, -0.36759)     (0.58036, 0.58036, 0.58036)   
9   (-0.46898, -0.40993, -0.24694)     (0.58036, 0.58036, 0.58036)   
10     (0.08049, 0.22710, 0.51224)     (0.58036, 0.58036, 0.51224)   
11     (0.58036, 0.58036, 0.58036)     (0.51224, 0.43642, 0.40993)   
12     (0.58036, 0.58036, 0.58036)     (0.34987, 0.29221, 0.23683)   

                                6                               7   \
0     (0.46898, 0.19116, -0.10077)    (0.58036, 0.31892, -0.01583)   
1   (-0.33375, -1.00000, -1.00000)  (-1.00000, -0.19116, -0.12174)   
2   (-1.00000, -1.00000, -0.58036)     (0.43642, 0.46898, 0.46898)   
3   (-0.33375, -0.10767, -0.02855)   (0.10767, -0.58036, -1.00000)   
4     (-0.00316, 0.02218, 0.04133)    (-0.14360, 0.16663, 0.30513)   
5     (0.04133, 0.05422, -0.04776)     (0.33375, 0.30513, 0.18279)   
6   (-0.22710, -0.46898, -0.51224)  (-0.11466, -0.13620, -0.08049)   
7    (-0.43642, -0.31892, 0.00316)    (-0.14360, 0.10767, 0.36759)   
8      (0.36759, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
9      (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
10     (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
11     (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   
12     (0.58036, 0.58036, 0.58036)     (0.58036, 0.58036, 0.58036)   

                                8                               9   \
0      (0.58036, 0.58036, 0.58036)    

In [13]:
tf_idfs = libword.tfidf(wordDfs, nwords=3)

In [14]:
tf_idfs[('X', 1)]

0                               1   \
0  (-1.00000, -0.33375, -0.17462)  (-0.58036, -1.00000, -0.30513)   
1  (-0.02218, -0.24694, -0.43642)     (0.46898, 0.15881, 0.46898)   
2     (0.51224, 0.33375, 0.04133)    (0.26847, 0.05422, -0.10077)   

                               2                               3   \
0  (-0.43642, -0.36759, -0.33375)  (-0.19975, -0.16663, -0.06726)   
1     (0.58036, 0.40993, 0.18279)   (-0.03492, -0.00950, 0.02218)   
2   (0.04776, -0.10077, -0.23683)  (-0.00950, -0.02855, -0.29221)   

                               4                             5   \
0   (-0.13620, -0.29221, 0.06726)   (0.25747, 0.13620, 0.06726)   
1  (-0.03492, -0.25747, -0.36759)  (-0.38737, 0.05422, 0.58036)   
2     (0.11466, 0.16663, 0.12174)   (0.43642, 0.30513, 0.40993)   

                               6                               7   \
0  (-0.33375, -0.10767, -0.02855)     (0.33375, 0.30513, 0.18279)   
1    (0.04133, 0.05422, -0.04776)    (-0.14360, 0.10767, 0.36759)   
2    (-0.00316, 0.02218, 0.04133)  (-1.00000, -0.19116, -0.12174)   

                               8                               9   \
0  (-1.00000, -1.00000, -1.00000)    (0.51224, 0.29221, -0.19975)   
1    (0.08718, 0.28002, -0.19116)    (-0.10077, 0.09394, 0.03492)   
2  (-0.51224, -0.31892, -0.58036)  (-0.58036, -1.00000, -0.19975)   

                              10                              11  \
0   (0.51224, 0.17462, -0.30513)  (-0.04776, -0.21769, -0.19975)   
1  (0.04776, -0.14360, -0.38737)    (-1.00000, 0.12174, 0.58036)   
2  (-0.14360, -0.13620, 0.15881)     (0.22710, 0.20859, 0.01583)   

                               12                              13  \
0     (0.38737, 0.43642, 0.46898)  (-0.51224, -0.43642, -0.26847)   
1     (0.31892, 0.58036, 0.51224)    (0.17462, 0.00950, -0.20859)   
2  (-0.21769, -0.16663, -0.13620)    (-0.13620, 0.05422, 0.29221)   

                               14                              15  \
0  (-0.40993, -0.31892, -0.29221)  (-0.05422, -0.10767, -0.24694)   
1   (0.03492, -0.40993, -1.00000)     (0.21769, 0.15114, 0.06072)   
2     (0.28002, 0.58036, 0.46898)    (-0.16663, 0.05422, 0.25747)   

                               16                              17  \
0   (-0.02855, -0.00316, 0.05422)     (0.58036, 0.33375, 0.29221)   
1   (0.03492, -0.31892, -1.00000)  (-0.14360, -0.16663, -0.10077)   
2  (-0.30513, -0.08049, -0.04133)    (-0.19975, 0.43642, 0.51224)   

                               18                              19  
0  (-1.00000, -0.46898, -0.16663)  (-0.58036, -1.00000, -1.00000)  
1    (-0.18279, 0.51224, 0.58036)     (0.51224, 0.51224, 0.58036)  
2   (-0.08049, 0.06072, -0.36759)   (0.04776, -0.02855, -0.36759)

In [15]:
g1 = odict((k,v) for k,v in wordDfs.items() if k[1] <= 31 )
g2 = odict((k,v) for k,v in wordDfs.items() if k[1] > 31 and k[1] < 280 )
g3 = odict((k,v) for k,v in wordDfs.items() if k[1] > 280 )


In [16]:
g1_tfidfs = libword.tfidf(g1, nwords=3)
g2_tfidfs = libword.tfidf(g2, nwords=3)
g3_tfidfs = libword.tfidf(g3, nwords=3)


In [17]:
g1_tfidfs[('X', 1)]

0                               1   \
0     (0.26847, 0.33375, 0.58036)     (0.46898, 0.15881, 0.46898)   
1  (-0.02218, -0.24694, -0.43642)    (0.26847, 0.05422, -0.10077)   
2     (0.51224, 0.33375, 0.04133)  (-0.58036, -1.00000, -0.30513)   

                               2                               3   \
0  (-0.43642, -0.36759, -0.33375)     (0.02855, 0.02855, 0.02855)   
1   (0.04776, -0.10077, -0.23683)   (-0.03492, -0.00950, 0.02218)   
2     (0.58036, 0.40993, 0.18279)  (-0.00950, -0.02855, -0.29221)   

                               4                               5   \
0  (-0.03492, -0.25747, -0.36759)  (-0.10767, -0.31892, -0.46898)   
1     (0.11466, 0.16663, 0.12174)    (-0.38737, 0.05422, 0.58036)   
2  (-1.00000, -0.43642, -0.08049)     (0.43642, 0.30513, 0.40993)   

                               6                               7   \
0  (-0.33375, -0.10767, -0.02855)     (0.33375, 0.30513, 0.18279)   
1    (0.04133, 0.05422, -0.04776)    (-0.14360, 0.10767, 0.36759)   
2    (-0.00316, 0.02218, 0.04133)  (-1.00000, -0.19116, -0.12174)   

                               8                               9   \
0  (-1.00000, -1.00000, -1.00000)    (-0.10077, 0.09394, 0.03492)   
1    (0.08718, 0.28002, -0.19116)  (-0.58036, -1.00000, -0.19975)   
2  (-0.51224, -0.31892, -0.58036)  (-0.19975, -0.31892, -0.46898)   

                              10                              11  \
0   (0.51224, 0.17462, -0.30513)  (-0.34987, -0.40993, -0.58036)   
1  (0.04776, -0.14360, -0.38737)     (0.22710, 0.20859, 0.01583)   
2  (-0.14360, -0.13620, 0.15881)  (-0.04776, -0.21769, -0.19975)   

                               12                              13  \
0     (0.31892, 0.58036, 0.51224)  (-0.51224, -0.43642, -0.26847)   
1  (-0.21769, -0.16663, -0.13620)    (0.17462, 0.00950, -0.20859)   
2     (0.38737, 0.43642, 0.46898)    (-0.13620, 0.05422, 0.29221)   

                              14                              15  \
0  (-0.29221, -0.12892, 0.06726)  (-0.05422, -0.10767, -0.24694)   
1  (0.03492, -0.40993, -1.00000)     (0.21769, 0.15114, 0.06072)   
2    (0.28002, 0.58036, 0.46898)    (-0.16663, 0.05422, 0.25747)   

                               16                              17  \
0   (-0.02855, -0.00316, 0.05422)     (0.58036, 0.33375, 0.29221)   
1   (0.03492, -0.31892, -1.00000)  (-0.14360, -0.16663, -0.10077)   
2  (-0.30513, -0.08049, -0.04133)    (-0.19975, 0.43642, 0.51224)   

                               18                              19  
0  (-1.00000, -0.46898, -0.16663)  (-0.58036, -1.00000, -1.00000)  
1    (-0.18279, 0.51224, 0.58036)     (0.51224, 0.51224, 0.58036)  
2   (-0.08049, 0.06072, -0.36759)   (0.04776, -0.02855, -0.36759)

In [20]:
import pickle
with open('wordDfs.pickle', 'wb') as fp:
    pickle.dump(wordDfs, fp)